In [45]:
import pandas as pd

In [46]:
import plotly.graph_objects as go

In [47]:
import plotly.express as px

In [48]:
def fix_time(x):
    if not '+' in x:
        return 0
    else:  
        s = x.split(' ')
        if 'min' in x:
            return 60*int(s[1]) + int(s[-2])
        else:
            return int(s[-2])

In [49]:
df_giro = pd.read_csv('./data/giro.csv', sep=';', names=['position','name','team','time'])

In [50]:
df_giro['position'] = df_giro['position'].apply(lambda x:int(x.split('.')[0]))

In [51]:
df_giro['country'] = df_giro['name'].apply(lambda x:x.split(' ')[0])

In [52]:
df_giro['name'] = df_giro['name'].apply(lambda x:' '.join(x.split(' ')[1:]))

In [53]:
df_giro.loc[(df_giro['time']!=df_giro['time'])]

Empty DataFrame
Columns: [position, name, team, time, country]
Index: []

In [54]:
df_giro['time'] = df_giro['time'].apply(fix_time)

In [55]:
dict_flags = {
    'ITA':'🇮🇹',
    'NOR':'🇳🇴',
    'POR':'🇵🇹',
    'FRA':'🇫🇷',
    'NED':'🇳🇱',
    'BEL':'🇧🇪',
    'GER':'🇩🇪',
    'AUT':'🇦🇹',
    'RUS':'🇷🇺',
    'ESP':'🇪🇸',
    'USA':'🇺🇸',
    'HUN':'🇭🇺',
    'GBR':'🇬🇧',
    'COL':'🇨🇴',
    'IRL':'🇮🇪'
}

In [56]:
df_giro['country'].unique()

array(['ITA', 'NOR', 'POR', 'FRA', 'NED', 'BEL', 'GER', 'AUT', 'RUS',
       'ESP', 'USA', 'HUN', 'GBR', 'COL', 'IRL'], dtype=object)

In [57]:
df_giro['country'] = df_giro['country'].apply(lambda x:dict_flags[x])

In [58]:
df_giro['name'] = df_giro['country'] + ' ' + df_giro['name']

In [59]:
top_5_names = df_giro.tail(10).head(5)

In [60]:
format_time = lambda x:f'{x//60} min {x%60} seg'

In [61]:
for name in top_5_names.to_dict(orient='records'):
    print(f'{name["position"]}. {name["name"]} - {name["team"]}: +{format_time(name["time"])}')

1. 🇨🇴 Egan Bernal - Ineos Grenadiers: +0 min 0 seg
2. 🇮🇹 Damiano Caruso - Bahrain Victorious: +1 min 29 seg
3. 🇬🇧 Simon Yates - Team BikeExchange: +4 min 15 seg
4. 🇷🇺 Aleksandr Vlasov - Astana-Premier Tech: +6 min 40 seg
5. 🇨🇴 Daniel Felipe Martínez - Ineos Grenadiers: +7 min 24 seg


In [62]:
top_5_names['name_position'] = top_5_names['position'].astype(str) + '. ' + top_5_names['name']

In [63]:
top_5_names.index = top_5_names['name']

In [64]:
top_5_names = top_5_names['name_position'].to_dict()

In [65]:
df_giro['name'] = df_giro['name'].apply(lambda x: top_5_names[x] if x in top_5_names else x)

In [66]:
stage = []
for n in range(len(df_giro)//10):
    stage = stage + [n+1]*10

In [67]:
df_giro['stage'] = stage

In [68]:
last_stage = df_giro['stage'].max()

In [69]:
df_giro = df_giro.loc[df_giro['stage']>=0]

In [70]:
names = df_giro.loc[
    (
        (df_giro['stage']==df_giro['stage'].max()) &
        (df_giro['position']<=5)
    ) #|
    #(
    #    (df_giro['position']==1)
    #)
]['name'].unique()

In [71]:
# df_giro = df_giro.loc[df_giro['name'].isin(names)]

In [72]:
df_giro = df_giro[
    [
        'name',
        'time',
        'stage'
    ]
]

In [73]:
time_max = df_giro['time'].max()

In [74]:
#time_max = (1+time_max//100)*100

In [75]:
time_max

1115

In [76]:
df_giro = df_giro.pivot(
    columns=['name'],
    index='stage'
)['time']

In [77]:
df_giro = df_giro.fillna(time_max+30)

In [78]:
df_index = (pd.Series(list(range(1,max(df_giro.index)*100+1,1)), name='stage')/100).to_frame()

In [79]:
df_index = df_index.loc[df_index['stage']>=0]

In [80]:
df_giro = df_giro.reset_index()

In [81]:
df_giro['stage'] = df_giro['stage'].astype(float)

In [82]:
df_giro = pd.merge(df_index, df_giro, on='stage', how='left')

In [83]:
df_giro = df_giro.fillna(method='bfill')

In [84]:
df_giro = df_giro.rolling(100, win_type='triang').mean()

In [85]:
df_giro

stage  1. 🇨🇴 Egan Bernal  2. 🇮🇹 Damiano Caruso  3. 🇬🇧 Simon Yates  \
0        NaN                NaN                   NaN                NaN   
1        NaN                NaN                   NaN                NaN   
2        NaN                NaN                   NaN                NaN   
3        NaN                NaN                   NaN                NaN   
4        NaN                NaN                   NaN                NaN   
...      ...                ...                   ...                ...   
2095  20.465                0.0                89.096           254.8336   
2096  20.475                0.0                89.054           254.9064   
2097  20.485                0.0                89.024           254.9584   
2098  20.495                0.0                89.006           254.9896   
2099  20.505                0.0                89.000           255.0000   

      4. 🇷🇺 Aleksandr Vlasov  5. 🇨🇴 Daniel Felipe Martínez  \
0                        NaN                           NaN   
1                        NaN                           NaN   
2                        NaN                           NaN   
3                        NaN                           NaN   
4                        NaN                           NaN   
...                      ...                           ...   
2095                400.0864                      444.1024   
2096                400.0486                      444.0576   
2097                400.0216                      444.0256   
2098                400.0054                      444.0064   
2099                400.0000                      444.0000   

      🇦🇹 Matthias Brändle  🇧🇪 Louis Vervaeke  🇧🇪 Remco Evenepoel  \
0                     NaN                NaN                 NaN   
1                     NaN                NaN                 NaN   
2                     NaN                NaN                 NaN   
3                     NaN                NaN                 NaN   
4                     NaN                NaN                 NaN   
...                   ...                ...                 ...   
2095               1145.0             1145.0              1145.0   
2096               1145.0             1145.0              1145.0   
2097               1145.0             1145.0              1145.0   
2098               1145.0             1145.0              1145.0   
2099               1145.0             1145.0              1145.0   

      🇩🇪 Emanuel Buchmann  ...  🇮🇹 Diego Ulissi  🇮🇹 Edoardo Affini  \
0                     NaN  ...              NaN                NaN   
1                     NaN  ...              NaN                NaN   
2                     NaN  ...              NaN                NaN   
3                     NaN  ...              NaN                NaN   
4                     NaN  ...              NaN                NaN   
...                   ...  ...              ...                ...   
2095               1145.0  ...           1145.0             1145.0   
2096               1145.0  ...           1145.0             1145.0   
2097               1145.0  ...           1145.0             1145.0   
2098               1145.0  ...           1145.0             1145.0   
2099               1145.0  ...           1145.0             1145.0   

      🇮🇹 Filippo Ganna  🇮🇹 Gianni Moscon  🇮🇹 Giulio Ciccone  🇳🇱 Jos van Emden  \
0                  NaN               NaN                NaN               NaN   
1                  NaN               NaN                NaN               NaN   
2                  NaN               NaN                NaN               NaN   
3                  NaN               NaN                NaN               NaN   
4                  NaN               NaN                NaN               NaN   
...                ...               ...                ...               ...   
2095            1145.0            1145.0             1145.0            1145.0   
2096            1145.0            1145.0   

In [86]:
fig = go.Figure()

top_5_color_list = [
    #'#4E79A7',
    '#A0CBE8',
    #'#F28E2B',
    '#9C755F',
    '#59A14F',
    '#EDC948'
]

for name in df_giro.columns:
    if name != 'stage':
        line_dict = {
            'width':0.6
        }
        is_leader = list(df_giro.loc[df_giro['stage']==df_giro['stage'].max()][name])[0]==0
        if (name in names) and not is_leader:
            line_dict['color']=top_5_color_list.pop()
            line_dict['width']=4
        if is_leader:
            line_dict['color']='#FF8BC1'
            line_dict['width']=9
        fig.add_trace(
            go.Scatter(
                #x=list(df_giro['stage']) + [int(list(df_giro['stage'])[-1]+1)],
                #y=list(df_giro[name]) + [list(df_giro[name])[-1]],
                x=df_giro['stage']+0.7,
                y=df_giro[name],
                name=name,
                line=line_dict
            )
        )

fig.update_layout(
    yaxis = dict(title='Diferencia con el líder (segundos)'),
    yaxis_range=[time_max+10, -5]
    #yaxis_range=[370, -5]
)
fig.update_layout(
    xaxis = dict(
        title = 'Etapa',
        tickmode = 'linear',
        tick0 = 1,
        dtick = 1
    ),
    yaxis = dict(
        tickmode = 'linear',
        dtick = 60
    )
)
fig.update_layout(
    title = '🚴 Giro de Italia 🎀 Top por etapa',
    title_x=0.25
)

#fig.update_layout(legend_title_text=f'Top 5 en etapa {last_stage}')
fig.update_layout(legend_title_text=f'Top 5 general')

for trace in fig['data']: 
    if (not trace['name'] in names):
        trace['showlegend'] = False
        
fig.layout.plot_bgcolor = '#eee'
fig.layout.paper_bgcolor = '#fff'

fig.show()

In [87]:
fig.write_html('../docs/giro.html')